In [1]:
import base64
import pandas as pd
import numpy as np
from scipy.io import wavfile
import io
import tensorflow as tf
from tensorflow.keras.models import load_model
import librosa
import pyaudio
import wave
import struct
import matplotlib.pyplot as plt
from scipy import signal
from scipy.io import wavfile 
# Load your model
model = tf.keras.models.load_model('models/echo_model/1/')


Metal device set to: Apple M1 Pro

systemMemory: 16.00 GB
maxCacheSize: 5.33 GB



In [2]:
# Define class names (it depends on your dataset)
class_names = ['class_1', 'class_2', 'class_3']  # Fill in the actual class names

CHUNK = 4096 
FORMAT = pyaudio.paInt16 #paInt8
CHANNELS = 1
RATE = 44100 #sample rate

p = pyaudio.PyAudio()

stream = p.open(format=FORMAT,
                channels=CHANNELS,
                rate=RATE,
                input=True,
                frames_per_buffer=CHUNK) #buffer

print("* recording")

def process_audio(audio_clip, sample_rate):
    frequencies, times, spectrogram = signal.spectrogram(audio_clip, sample_rate)
    plt.pcolormesh(times, frequencies, 10 * np.log10(spectrogram))
    plt.imshow(10 * np.log10(spectrogram))
    plt.axis('off')
    plt.savefig("spectrogram.png")
    plt.close()

    img = tf.keras.preprocessing.image.load_img("spectrogram.png", target_size=(64, 64))
    img_array = tf.keras.preprocessing.image.img_to_array(img)
    img_array = tf.expand_dims(img_array, 0)
    return img_array


def predict_class(predictions, class_names):
    predicted_class = np.argmax(predictions)
    predicted_probability = np.max(predictions)
    return class_names[predicted_class], predicted_probability

# Create an empty DataFrame to hold the results
results_df = pd.DataFrame(columns=['Timestamp', 'Predicted Class', 'Probability'])
while True:
    data = stream.read(CHUNK)
    audio_clip = np.frombuffer(data, dtype=np.int16) / np.iinfo(np.int16).max
    
    # Process the audio clip
    image = process_audio(audio_clip, RATE)

    # If the image is grayscale, repeat it across 3 channels to create a 3-channel image
    if image.shape[-1] == 1:
        image = tf.repeat(image, repeats=3, axis=-1)

    # Resize image to match the size expected by the model
    image = tf.image.resize(image, [260, 260])
    
    # The image must be 4D: (batch_size, height, width, channels)
    image = tf.expand_dims(image, axis=0)

    # Make the model prediction
    predictions = model.predict(image)

    # Predict class and probability
    predicted_class, predicted_probability = predict_class(predictions, class_names)

    # Add the result to the DataFrame
    results_df = results_df.append({
        'Timestamp': pd.Timestamp.now(),
        'Predicted Class': predicted_class,
        'Probability': predicted_probability
    }, ignore_index=True)

    # Print the results every CHUNK
    if len(results_df) % CHUNK == 0:
        print(results_df.tail(CHUNK))

print("* done recording")


stream.stop_stream()
stream.close()
p.terminate()

* recording


/var/folders/tp/jx74xxwd0qgct2nvjkzx_m1h0000gn/T/ipykernel_1936/2067140287.py:21: RuntimeWarning: divide by zero encountered in log10
  plt.pcolormesh(times, frequencies, 10 * np.log10(spectrogram))
/var/folders/tp/jx74xxwd0qgct2nvjkzx_m1h0000gn/T/ipykernel_1936/2067140287.py:22: RuntimeWarning: divide by zero encountered in log10
  plt.imshow(10 * np.log10(spectrogram))
2023-07-22 14:19:48.681523: W tensorflow/tsl/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz


ValueError: in user code:

    File "/Users/ankush/anaconda3/envs/new_env/lib/python3.8/site-packages/keras/engine/training.py", line 2169, in predict_function  *
        return step_function(self, iterator)
    File "/Users/ankush/anaconda3/envs/new_env/lib/python3.8/site-packages/keras/engine/training.py", line 2155, in step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    File "/Users/ankush/anaconda3/envs/new_env/lib/python3.8/site-packages/keras/engine/training.py", line 2143, in run_step  **
        outputs = model.predict_step(data)
    File "/Users/ankush/anaconda3/envs/new_env/lib/python3.8/site-packages/keras/engine/training.py", line 2111, in predict_step
        return self(x, training=False)
    File "/Users/ankush/anaconda3/envs/new_env/lib/python3.8/site-packages/keras/utils/traceback_utils.py", line 70, in error_handler
        raise e.with_traceback(filtered_tb) from None
    File "/Users/ankush/anaconda3/envs/new_env/lib/python3

In [16]:
import threading
from skimage.transform import resize


In [18]:
# Define class names (it depends on your dataset)
class_names = ['class_1', 'class_2', 'class_3']  # Fill in the actual class names

CHUNK = 8192  # increase this
FORMAT = pyaudio.paInt16
CHANNELS = 1
RATE = 48000  # sample rate

p = pyaudio.PyAudio()

stream = p.open(format=FORMAT,
                channels=CHANNELS,
                rate=RATE,
                input=True,
                frames_per_buffer=CHUNK)  # buffer

print("* recording")

run_flag = True  # global flag

def process_audio(audio_clip, sample_rate):
    frequencies, times, spectrogram = signal.spectrogram(audio_clip, nfft=2048, noverlap=200, fs=sample_rate)
    spectrogram = 10 * np.log10(spectrogram)

    # Resize the spectrogram to match your model's input shape
    # Here I'm assuming your model expects a 260x260x3 image.
    spectrogram = resize(spectrogram, (260, 260))[:, :, np.newaxis]
    spectrogram = np.repeat(spectrogram, 3, axis=2)

    return spectrogram

def predict_class(predictions, class_names):
    predicted_class = np.argmax(predictions)
    predicted_probability = np.max(predictions)
    return class_names[predicted_class], predicted_probability

def process_audio_stream():
    global run_flag
    results_df = pd.DataFrame(columns=['Timestamp', 'Predicted Class', 'Probability'])
    while run_flag:
        try:
            data = stream.read(CHUNK)
            audio_clip = np.frombuffer(data, dtype=np.int16) / np.iinfo(np.int16).max

            # Process the audio clip
            image = process_audio(audio_clip, RATE)

            # The image must be 4D: (batch_size, height, width, channels)
            image = np.expand_dims(image, axis=0)

            # Make the model prediction
            predictions = model.predict(image)

            # Predict class and probability
            predicted_class, predicted_probability = predict_class(predictions, class_names)

            # Add the result to the DataFrame
            results_df = results_df.append({
                'Timestamp': pd.Timestamp.now(),
                'Predicted Class': predicted_class,
                'Probability': predicted_probability
            }, ignore_index=True)

            # Print the results every CHUNK
            if len(results_df) % CHUNK == 0:
                print(results_df.tail(CHUNK))
        except Exception as e:
            print(f"Error: {e}")

    stream.stop_stream()
    stream.close()
    p.terminate()
    print("* done recording")


thread = threading.Thread(target=process_audio_stream)
thread.start()

input("Press enter to stop")

run_flag = False

thread.join()

* recording
1/1 [==============================] - 0s 356ms/step
Error: [Errno -9981] Input overflowed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] S

/var/folders/tp/jx74xxwd0qgct2nvjkzx_m1h0000gn/T/ipykernel_1936/3023880975.py:58: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({


Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988] Stream closed
Error: [Errno -9988]

Exception in thread Thread-13:
Traceback (most recent call last):
  File "/Users/ankush/anaconda3/envs/new_env/lib/python3.8/threading.py", line 932, in _bootstrap_inner
    self.run()
  File "/Users/ankush/anaconda3/envs/new_env/lib/python3.8/threading.py", line 870, in run
    self._target(*self._args, **self._kwargs)
  File "/var/folders/tp/jx74xxwd0qgct2nvjkzx_m1h0000gn/T/ipykernel_1936/3023880975.py", line 70, in process_audio_stream
  File "/Users/ankush/anaconda3/envs/new_env/lib/python3.8/site-packages/pyaudio/__init__.py", line 500, in stop_stream
    pa.stop_stream(self._stream)
OSError: Stream not open


In [13]:
results_df

Empty DataFrame
Columns: [Timestamp, Predicted Class, Probability]
Index: []